<a href="https://colab.research.google.com/github/bkkaggle/pytorch-CycleGAN-and-pix2pix/blob/master/pix2pix.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive

drive.mount('/content/gdrive/')

Mounted at /content/gdrive/


Prepare data - Need to run only one time. Make image pairs and split in train and test

In [2]:
class ArgsData:
  #fold_A = '/content/gdrive/MyDrive/CXR_png'
  #fold_B = '/content/gdrive/MyDrive/CXR_images_masks'
  fold_AB = '/content/gdrive/MyDrive/pix2pix/data/CXR_images_combined'
  num_imgs = 1000000
  use_AB = True
  n_folds = 10
  checkpoint = False
  fold_checkpoint = 1
  experimento_1a_vez = True
  exp_name = "tb"
  seed = 0

In [1]:
#import wandb
#wandb.util.generate_id(seed=0)

In [ ]:
import os
import sys
import tensorflow as tf
import numpy as np
import glob
import logging

from tensorflow.keras.callbacks import Callback
from sklearn.metrics import roc_curve
from collections import Counter


def load_filenames(data_dir, dataset_name):
    """
    Read png data and return X and y vectors for model training.
    """
    input_files = dict()

    if dataset_name == 'schenzen':
        file_name = 'CHNCXR_*_0.png'
        input_files['H0'] = glob.glob(os.path.join(data_dir, file_name))
        file_name = 'CHNCXR_*_1.png'
        input_files['H1'] = glob.glob(os.path.join(data_dir, file_name))

        n_H0 = len(input_files['H0'])
        n_H1 = len(input_files['H1'])

        X = np.asarray(input_files['H0'] + input_files['H1'])
        y = np.concatenate((np.zeros(n_H0), np.ones(n_H1)))
    else:
        print('Error! Not valid dataset name.')
        sys.exit()

    return X, y


In [ ]:
X, y = load_filenames('/content/gdrive/MyDrive/CXR_png', dataset_name='schenzen')
X_masks, y_masks = load_filenames('/content/gdrive/MyDrive/CXR_images_masks', dataset_name='schenzen')

cont = 0
X_imgs_masks = []
y_imgs_masks = []
X_imgs = []
y_imgs = []
for img_mask in X_masks:
  for img in X:
    if img_mask[-17:] == img[-17:]:
      X_imgs_masks.append(img_mask)
      X_imgs.append(img)
      y_imgs.append(y[cont])
      y_imgs_masks.append(y_masks[cont])
      cont += 1

X_imgs = np.array(X_imgs)
y_imgs = np.array(y_imgs)
X_imgs_masks = np.array(X_imgs_masks)
y_imgs_masks = np.array(y_imgs_masks)


In [ ]:
import os
import numpy as np
import cv2
import argparse
from sklearn.model_selection import StratifiedKFold

args = ArgsData()


skf_trainval_test = StratifiedKFold(n_splits=args.n_folds, shuffle=True, random_state= args.seed)
skf_trainval_test.get_n_splits(X_imgs,y_imgs)
X_trainval, X_test, y_trainval, y_test, X_masks_trainval, X_masks_test, y_masks_trainval, y_masks_test = [],[],[],[],[],[],[],[]
for trainval_index, test_index in skf_trainval_test.split(X_imgs,y_imgs):
  print("TRAIN:", len(trainval_index), "TEST:", len(test_index))
  X_trainval.append(X_imgs[trainval_index])
  y_trainval.append(y_imgs[trainval_index])
  X_test.append(X_imgs[test_index])
  y_test.append(y_imgs[test_index])

  ##Masks

  X_masks_trainval.append(X_imgs_masks[trainval_index])
  y_masks_trainval.append(y_imgs_masks[trainval_index])
  X_masks_test.append(X_imgs_masks[test_index])
  y_masks_test.append(y_imgs_masks[test_index])


#for fold in range(args.n_folds):
#  img_fold_AB = args.fold_AB + '_' + str(fold)
#  if not os.path.isdir(img_fold_AB):
#    os.makedirs(img_fold_AB)


TRAIN: 509 TEST: 57
TRAIN: 509 TEST: 57
TRAIN: 509 TEST: 57
TRAIN: 509 TEST: 57
TRAIN: 509 TEST: 57
TRAIN: 509 TEST: 57
TRAIN: 510 TEST: 56
TRAIN: 510 TEST: 56
TRAIN: 510 TEST: 56
TRAIN: 510 TEST: 56


Generating TRAINVAL splits for trainning

In [ ]:
#import os
#import numpy as np
#import cv2
#import argparse


#for fold in range(args.n_folds):
  
  #for arg in vars(args):
  #  print('[%s] = ' % arg, getattr(args, arg))
  
  
  #img_list = [img_path for img_path in X_trainval[fold] if 'CHNCXR_' in img_path]
  #num_imgs = min(args.num_imgs, len(img_list))
  
  #img_fold_AB = args.fold_AB + '_' + str(fold)
  #if not os.path.isdir(img_fold_AB):
  #  os.makedirs(img_fold_AB)
  
  #for n in range(num_imgs):
  #  path_A = img_list[n]
  #  path_B = X_masks_trainval[fold][n]
  #  if os.path.isfile(path_A) and os.path.isfile(path_B):
  #    name_file = path_A[-17:]
  #    path_AB = os.path.join(img_fold_AB, name_file)
  #    im_A = cv2.imread(path_A)
  #    im_B = cv2.imread(path_B)
  #    im_AB = np.concatenate([im_B, im_A], 1)
  #    cv2.imwrite(path_AB, im_AB)

In [ ]:
from sklearn.model_selection import train_test_split

for fold in range(args.n_folds):
  
  #for arg in vars(args):
  #  print('[%s] = ' % arg, getattr(args, arg))
  
  X_train_aux, X_val_aux, y_train_aux, y_val_aux = train_test_split(X_trainval[fold], y_trainval[fold], test_size=0.1, random_state=args.seed)
  X_masks_train_aux, X_masks_val_aux, y_masks_train_aux, y_masks_val_aux = train_test_split(X_masks_trainval[fold], y_masks_trainval[fold], test_size=0.1, random_state=args.seed)
  
  img_list_train = [img_path for img_path in X_train_aux if 'CHNCXR_' in img_path]
  num_imgs_train = min(args.num_imgs, len(img_list_train))
  
  img_list_val = [img_path for img_path in X_val_aux if 'CHNCXR_' in img_path]
  num_imgs_val = min(args.num_imgs, len(img_list_val))
  
  img_fold_AB_train = args.fold_AB + '_' + str(fold) + '/train'
  img_fold_AB_val = args.fold_AB + '_' + str(fold) + '/val'
  if not os.path.isdir(img_fold_AB_train):
    os.makedirs(img_fold_AB_train)
  
  if not os.path.isdir(img_fold_AB_val):
    os.makedirs(img_fold_AB_val)
  
  for n_train in range(num_imgs_train):
    path_A_train = img_list_train[n_train]
    path_B_train = X_masks_train_aux[n_train]
    if os.path.isfile(path_A_train) and os.path.isfile(path_B_train):
      name_file = path_A_train[-17:]
      path_AB_train = os.path.join(img_fold_AB_train, name_file)
      im_A = cv2.imread(path_A_train)
      im_B = cv2.imread(path_B_train)
      im_AB = np.concatenate([im_B, im_A], 1)
      cv2.imwrite(path_AB_train, im_AB)
  
  for n_val in range(num_imgs_val):
    path_A_val = img_list_val[n_val]
    path_B_val = X_masks_val_aux[n_val]
    if os.path.isfile(path_A_val) and os.path.isfile(path_B_val):
      name_file = path_A_val[-17:]
      path_AB_val = os.path.join(img_fold_AB_val, name_file)
      im_A = cv2.imread(path_A_val)
      im_B = cv2.imread(path_B_val)
      im_AB = np.concatenate([im_B, im_A], 1)
      cv2.imwrite(path_AB_val, im_AB)

Genarating Test folds for model evaluation 

In [ ]:
for fold in range(args.n_folds):
  
  #for arg in vars(args):
  #  print('[%s] = ' % arg, getattr(args, arg))

  img_list = [img_path for img_path in X_test[fold] if 'CHNCXR_' in img_path]
  num_imgs = min(args.num_imgs, len(img_list))
  
  img_fold_AB_test = args.fold_AB + '_' + str(fold) + '/test'
  if not os.path.isdir(img_fold_AB_test):
    os.makedirs(img_fold_AB_test)
  
  for n in range(num_imgs):
    path_A = img_list[n]
    path_B = X_masks_test[fold][n]
    if os.path.isfile(path_A) and os.path.isfile(path_B):
      name_file = path_A[-17:]
      path_AB_test = os.path.join(img_fold_AB_test, name_file)
      im_A = cv2.imread(path_A)
      im_B = cv2.imread(path_B)
      im_AB = np.concatenate([im_B, im_A], 1)
      cv2.imwrite(path_AB_test, im_AB)

Training - Import a fold of training data 

In [ ]:
for fold in range(args.n_folds):
  
  img_fold_AB = args.fold_AB + '_' + str(fold)
  X, y = load_filenames(img_fold_AB , dataset_name='schenzen')
  X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.33, random_state=42)
  if os.path.isfile(path_A) and os.path.isfile(path_B):
    name_file = path_A[-17:]
    path_AB = os.path.join(img_fold_AB, name_file)
    im_A = cv2.imread(path_A)
    im_B = cv2.imread(path_B)
    im_AB = np.concatenate([im_B, im_A], 1)
    cv2.imwrite(path_AB, im_AB)

Generating data folders for TB and NTB classes

In [ ]:
args = ArgsData()
import cv2
for fold in range(args.n_folds):

  #train
  X_train, y_train = load_filenames(args.fold_AB + '_' + str(fold) + '/train', dataset_name='schenzen')
  X_train_tb = X_train[y_train == 1]
  X_train_ntb = X_train[y_train == 0]
  img_fold_AB_train_tb = args.fold_AB + '_' + str(fold) + '/TB/train'
  img_fold_AB_train_ntb = args.fold_AB + '_' + str(fold) + '/NTB/train'

  if not os.path.isdir(img_fold_AB_train_tb):
    os.makedirs(img_fold_AB_train_tb)
  
  if not os.path.isdir(img_fold_AB_train_ntb):
    os.makedirs(img_fold_AB_train_ntb)
  
  for img in X_train_tb:
    img_nm = img[-17:]
    path_train_tb = os.path.join(img_fold_AB_train_tb, img_nm)
    im_A = cv2.imread(img)
    cv2.imwrite(path_train_tb, im_A)
  
  for img in X_train_ntb:
    img_nm = img[-17:]
    path_train_ntb = os.path.join(img_fold_AB_train_ntb, img_nm)
    im_A = cv2.imread(img)
    cv2.imwrite(path_train_ntb, im_A)
  
  
  
  #val
  X_val, y_val = load_filenames(args.fold_AB + '_' + str(fold) + '/val', dataset_name='schenzen')
  X_val_tb = X_val[y_val == 1]
  X_val_ntb = X_val[y_val == 0]
  img_fold_AB_val_tb = args.fold_AB + '_' + str(fold) + '/TB/val'
  img_fold_AB_val_ntb = args.fold_AB + '_' + str(fold) + '/NTB/val'

  if not os.path.isdir(img_fold_AB_val_tb):
    os.makedirs(img_fold_AB_val_tb)

  if not os.path.isdir(img_fold_AB_val_ntb):
    os.makedirs(img_fold_AB_val_ntb)

  for img in X_val_tb:
    img_nm = img[-17:]
    path_val_tb = os.path.join(img_fold_AB_val_tb, img_nm)
    im_A = cv2.imread(img)
    cv2.imwrite(path_val_tb, im_A)
  
  for img in X_val_ntb:
    img_nm = img[-17:]
    path_val_ntb = os.path.join(img_fold_AB_val_ntb, img_nm)
    im_A = cv2.imread(img)
    cv2.imwrite(path_val_ntb, im_A)
  


  #test
  X_test, y_test = load_filenames(args.fold_AB + '_' + str(fold) + '/test', dataset_name='schenzen')
  X_test_tb = X_test[y_test == 1]
  X_test_ntb = X_test[y_test == 0]
  img_fold_AB_test_tb = args.fold_AB + '_' + str(fold) + '/TB/test'
  img_fold_AB_test_ntb = args.fold_AB + '_' + str(fold) + '/NTB/test'
  
  if not os.path.isdir(img_fold_AB_test_tb):
    os.makedirs(img_fold_AB_test_tb)

  if not os.path.isdir(img_fold_AB_test_ntb):
    os.makedirs(img_fold_AB_test_ntb)
  
  for img in X_test_tb:
    img_nm = img[-17:]
    path_test_tb = os.path.join(img_fold_AB_test_tb, img_nm)
    im_A = cv2.imread(img)
    cv2.imwrite(path_test_tb, im_A)
  
  for img in X_test_ntb:
    img_nm = img[-17:]
    path_test_ntb = os.path.join(img_fold_AB_test_ntb, img_nm)
    im_A = cv2.imread(img)
    cv2.imwrite(path_test_ntb, im_A)
  
  


# Install

In [ ]:
#!git clone https://github.com/junyanz/pytorch-CycleGAN-and-pix2pix

In [3]:
import os
os.chdir('gdrive/MyDrive/pix2pix/pix2pixTB/pytorch-CycleGAN-and-pix2pix/')

In [4]:
!pip install -r requirements.txt

     |████████████████████████████████| 676 kB 10.4 MB/s 
     |████████████████████████████████| 1.7 MB 74.9 MB/s 
     |████████████████████████████████| 53 kB 2.8 MB/s 
     |████████████████████████████████| 180 kB 79.9 MB/s 
     |████████████████████████████████| 143 kB 93.0 MB/s 
     |████████████████████████████████| 97 kB 9.7 MB/s 
     |████████████████████████████████| 63 kB 2.4 MB/s 
  Created wheel for visdom: filename=visdom-0.1.8.9-py3-none-any.whl size=655250 sha256=f8fae2c952b3b11dce60379c28ce443569181a727f0770ffe3b4a27adabe7e58
  Stored in directory: /root/.cache/pip/wheels/2d/d1/9b/cde923274eac9cbb6ff0d8c7c72fe30a3da9095a38fd50bbf1
  Created wheel for subprocess32: filename=subprocess32-3.5.4-py3-none-any.whl size=6502 sha256=ce80e4bc92f06987fec11b6453819ae59351c74b3a510f599ff323d9f92d9d0c
  Stored in directory: /root/.cache/pip/wheels/50/ca/fa/8fca8d246e64f19488d07567547ddec8eb084e8c0d7a59226a
  Created wheel for pathtools: filename=pathtools-0.1.2-py3-none-any.whl

# Datasets

Download one of the official datasets with:

-   `paired images from shenzhen`

- After pairing images, and spliting in folds, data is ready for trainning

# Training

-   `python train.py --dataroot ./datasets/facades --name facades_pix2pix --model pix2pix --direction BtoA`

Change the `--dataroot` and `--name` to your own dataset's path and model's name. Use `--gpu_ids 0,1,..` to train on multiple GPUs and `--batch_size` to change the batch size. Add `--direction BtoA` if you want to train a model to transfrom from class B to A.

FOLD 0

TB

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/TB --model pix2pix --direction AtoB --gpu_ids 0 --gan_mode wgangp --use_wandb --n_epochs 500 --n_epochs_decay 500

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: False                         
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/TB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epoch: latest        

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/TB --model pix2pix --direction AtoB --gpu_ids 0  --use_wandb --n_epochs 1000 --n_epochs_decay 1000

Streaming output truncated to the last 5000 lines.
/usr/local/lib/python3.7/dist-packages/torchvision/transforms/transforms.py:288: UserWarning: Argument interpolation should be of type InterpolationMode instead of int. Please, use InterpolationMode enum.
  "Argument interpolation should be of type InterpolationMode instead of int. "
(epoch: 899, iters: 62, time: 0.072, data: 0.412) G_GAN: 5.891 G_L1: 5.772 D_real: 0.012 D_fake: 0.010 
(epoch: 899, iters: 162, time: 4.045, data: 0.002) G_GAN: 2.742 G_L1: 4.114 D_real: 0.388 D_fake: 0.202 
End of epoch 899 / 2000 	 Time Taken: 45 sec
learning rate 0.0002000 -> 0.0002000
/usr/local/lib/python3.7/dist-packages/torchvision/transforms/transforms.py:288: UserWarning: Argument interpolation should be of type InterpolationMode instead of int. Please, use InterpolationMode enum.
  "Argument interpolation should be of type InterpolationMode instead of int. "
/usr/local/lib/python3.7/dist-packages/torchvision/transforms/transforms.py:288: UserWar

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/TB --model pix2pix --direction AtoB --continue_train --epoch_count 1297 --gpu_ids 0  --use_wandb --n_epochs 1000 --n_epochs_decay 1000

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: True                          	[default: False]
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/TB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epoc

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/TB --model pix2pix --direction AtoB --continue_train --epoch_count 1632 --gpu_ids 0  --use_wandb --n_epochs 1000 --n_epochs_decay 1000

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: True                          	[default: False]
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/TB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epoc

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/TB --model pix2pix --direction AtoB --continue_train --epoch_count 1967 --gpu_ids 0  --use_wandb --n_epochs 1000 --n_epochs_decay 1000

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: True                          	[default: False]
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/TB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epoc

NTB

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB --model pix2pix --direction AtoB --gpu_ids 0 --gan_mode wgangp --use_wandb --name wgan_ntb_500iter_500decay --n_epochs 500 --n_epochs_decay 500

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: False                         
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epoch: latest       

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB --model pix2pix --direction AtoB --continue_train --epoch_count 8 --gpu_ids 0 --gan_mode wgangp --use_wandb --isResume_wandb True --name wgan_ntb_500iter_500decay --n_epochs 500 --n_epochs_decay 500

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: True                          	[default: False]
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epo

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB --model pix2pix --direction AtoB --gpu_ids 0  --use_wandb --name fold0_ntb  --n_epochs 1000 --n_epochs_decay 1000

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: False                         
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epoch: latest       

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB --model pix2pix --continue_train --epoch_count 342 --direction AtoB --gpu_ids 0  --use_wandb --isResume_wandb True --name fold0_ntb  --n_epochs 1000 --n_epochs_decay 1000

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: True                          	[default: False]
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epo

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB --model pix2pix --continue_train --epoch_count 527 --direction AtoB --gpu_ids 0  --use_wandb --name fold0_ntb  --n_epochs 1000 --n_epochs_decay 1000

Streaming output truncated to the last 5000 lines.
/usr/local/lib/python3.7/dist-packages/torchvision/transforms/transforms.py:288: UserWarning: Argument interpolation should be of type InterpolationMode instead of int. Please, use InterpolationMode enum.
  "Argument interpolation should be of type InterpolationMode instead of int. "
/usr/local/lib/python3.7/dist-packages/torchvision/transforms/transforms.py:288: UserWarning: Argument interpolation should be of type InterpolationMode instead of int. Please, use InterpolationMode enum.
  "Argument interpolation should be of type InterpolationMode instead of int. "
/usr/local/lib/python3.7/dist-packages/torchvision/transforms/transforms.py:288: UserWarning: Argument interpolation should be of type InterpolationMode instead of int. Please, use InterpolationMode enum.
  "Argument interpolation should be of type InterpolationMode instead of int. "
(epoch: 654, iters: 71, time: 0.053, data: 0.001) G_GAN: 4.296 G_L1: 5.314 Wasserstein: 4.263 

In [ ]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB --model pix2pix --continue_train --epoch_count 1124 --direction AtoB --gpu_ids 0  --use_wandb --name fold0_ntb  --n_epochs 1000 --n_epochs_decay 1000

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: True                          	[default: False]
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epo

In [4]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB --model pix2pix --continue_train --epoch_count 1465 --direction AtoB --gpu_ids 0  --use_wandb --name fold0_ntb  --n_epochs 1000 --n_epochs_decay 1000

A saída de streaming foi truncada nas últimas 5000 linhas.
    self._sm.finish()
  File "/usr/local/lib/python3.7/dist-packages/wandb/sdk/internal/sender.py", line 1074, in finish
    self._dir_watcher.finish()
  File "/usr/local/lib/python3.7/dist-packages/wandb/filesync/dir_watcher.py", line 327, in finish
    logger.info("scan save: %s %s", file_path, save_name)
Message: 'scan save: %s %s'
Arguments: ('/content/gdrive/MyDrive/pix2pix/pix2pixTB/pytorch-CycleGAN-and-pix2pix/wandb/run-20220125_142411-34n5p2rq/files/media/images/real_B_1077_91d137d9f231ec5ac31f.png', 'media/images/real_B_1077_91d137d9f231ec5ac31f.png')
--- Logging error ---
Traceback (most recent call last):
  File "/usr/lib/python3.7/logging/__init__.py", line 1029, in emit
    self.flush()
  File "/usr/lib/python3.7/logging/__init__.py", line 1009, in flush
    self.stream.flush()
OSError: [Errno 107] Transport endpoint is not connected
Call stack:
  File "/usr/lib/python3.7/threading.py", line 890, in _bootstrap
    

In [4]:
#!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB --model pix2pix --continue_train --epoch_count 1792 --direction AtoB --gpu_ids 0  --use_wandb --name fold0_ntb  --n_epochs 1000 --n_epochs_decay 1000

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: True                          	[default: False]
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_0/NTB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epo

FOLD 1


TB


In [5]:
#import wandb
#mport pickle
#args = ArgsData()
#wandb_ids = []
#fold_1a_vez = 1
#if args.checkpoint:
#  exp_nm = args.exp_name + "_wandb_fold_ids.pkl"
#  expIDs = open(os.getcwd() + '/wandb/' + exp_nm, "rb")
#  ids = pickle.load(expIDs)
#  wandb_fold_id = ids['fold_ids'][args.fold_checkpoint]
#  os.chdir('..')
#else:
#  if args.experimento_1a_vez:
#    os.chdir(os.getcwd() + '/wandb')
#    exp_nm = args.exp_name + "_wandb_fold_ids.pkl"
#    for fold in range(args.n_folds):
#      wandb_ids.append(wandb.util.generate_id())
#    expIDs = { "fold_ids": wandb_ids }
#    exp_file = open(exp_nm, "wb" )
#    pickle.dump(expIDs, exp_file)
#    exp_file.close()
#    os.chdir('..')
#    wandb_fold_id = wandb_ids[fold_1a_vez]
#  else:
#    exp_nm = args.exp_name + "_wandb_fold_ids.pkl"
#    expIDs = open(os.getcwd() + '/wandb/' + exp_nm, "rb")
#    ids = pickle.load(expIDs)
#    wandb_fold_id = ids['fold_ids'][args.fold_checkpoint]
#    os.chdir('..')


In [ ]:
!python train.py --dataroot /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_1/TB --model pix2pix --direction AtoB --gpu_ids 0  --use_wandb --wandb_fold_id wandb_tb_fold_1 --is_resume_wandb False --name fold1_tb  --n_epochs 1000 --n_epochs_decay 1000

----------------- Options ---------------
               batch_size: 1                             
                    beta1: 0.5                           
          checkpoints_dir: ./checkpoints                 
           continue_train: False                         
                crop_size: 256                           
                 dataroot: /content/gdrive/MyDrive/pix2pix/data/CXR_images_combined_1/TB	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
              display_env: main                          
             display_freq: 400                           
               display_id: 1                             
            display_ncols: 4                             
             display_port: 8097                          
           display_server: http://localhost              
          display_winsize: 256                           
                    epoch: latest        

# Testing

-   `python test.py --dataroot ./datasets/facades --direction BtoA --model pix2pix --name facades_pix2pix`

Change the `--dataroot`, `--name`, and `--direction` to be consistent with your trained model's configuration and how you want to transform images.

> from https://github.com/junyanz/pytorch-CycleGAN-and-pix2pix:
> Note that we specified --direction BtoA as Facades dataset's A to B direction is photos to labels.

> If you would like to apply a pre-trained model to a collection of input images (rather than image pairs), please use --model test option. See ./scripts/test_single.sh for how to apply a model to Facade label maps (stored in the directory facades/testB).

> See a list of currently available models at ./scripts/download_pix2pix_model.sh

In [ ]:
!ls checkpoints/

In [ ]:
!python test.py --dataroot ./datasets/facades --direction BtoA --model pix2pix --name facades_label2photo_pretrained --use_wandb

# Visualize

In [ ]:
import matplotlib.pyplot as plt

img = plt.imread('./results/facades_label2photo_pretrained/test_latest/images/100_fake_B.png')
plt.imshow(img)

In [ ]:
img = plt.imread('./results/facades_label2photo_pretrained/test_latest/images/100_real_A.png')
plt.imshow(img)

In [ ]:
img = plt.imread('./results/facades_label2photo_pretrained/test_latest/images/100_real_B.png')
plt.imshow(img)